In [1]:
# procedure for calculating hydraulic confinement along a pressure tunnel 
# completed procedure will in the form of a design report
#   safety factor against hydraulic confinement calculated at stationed points along tunnel alignment
#   calculation determines the minimum dstance from the stationed point to the terrain surface 

# project name: 'Snow Mountain 2.0 PSP' 

In [2]:
# ToDo
#   DONE need to read in 'slope' and get slope values for all buffer grid points 'MIN'
#   DONE Nam Ang headrace tunnel alignment and DTM
#   DONE add calculation for hydraulic confinement safety factor (SF)
#   DONE add results plot for hydraulic confinement safety factor
#   put common functions (e.g. setup, data format conversions) into a separate module/API
#   DONE use Nam Ang HEP data for initial testing and demo
#   provide full desgin criteria text in Jupyter Notebook design report
#   DONE add check plot with alignment, station points, buffer points
#   DONE add check plot with MIN buffer grid points
#   refactor code

In [3]:
# import required python libraires
import numpy as np
from numpy import *
import pandas as pd
import geopandas as gpd
import shapely as sp
#import matplotlib.pylab as pylab  #matplotlib not currently used
#import matplotlib.pyplot as plt
#%matplotlib inline

# testing
#import random
# check pd and gpd version
#print(pd.__version__)
#print(gpd.__version__)

In [4]:
# python setup for qgis processing
import sys, os
from qgis.core import QgsApplication
from PyQt4.QtGui import QApplication
app = QApplication([], True)  #True -> window display enabled
QgsApplication.setPrefixPath("/usr", True)
QgsApplication.initQgis()
sys.path.append('/usr/share/qgis/python/plugins')  #export PYTHONPATH not needed in start script
from processing.core.Processing import Processing
Processing.initialize() 
import processing
#from processing.tools import *  #not needed currently

In [5]:
# set up plotly in 'offline' mode                            #ToDo JK: this should be cleaned up and documented
from plotly import __version__
from plotly.offline import download_plotlyjs, init_notebook_mode, plot,iplot
import plotly.graph_objs as go
init_notebook_mode(connected=True)
print (__version__) # requires version >= 1.9.0

# collect all plotly setups here
import plotly.offline as plotly
from plotly.graph_objs import *

2.2.1


In [6]:
# import DSS modules
#import geospatial as geo

In [7]:
# set wd for this procedure and project 
os.chdir("/home/kaelin_joseph/DSS.HydraulicConfinement/")

In [8]:
# set maximum number of rows to display from a pandas data frame
#pd.set_option('display.max_rows', 3000)
pd.set_option('display.max_rows', 30000)

In [9]:
# define required input files
# Snowy Mountain 2.0 PSP
# alignment data will be defined direclty in Jupyter Notebook, to better document alternatives studied
##Alignment = "data/in/SnowMountains2.WaterwaysAlignment.r2.csv"  
DTM = "data/in/SnowyMountainsTopogRaster.tif"  #DEM with surface topography
#   Alignment contains fields "Point","Type","Station","Northing","Easting","Elevation"
#   check Alignment data: no spaces between comma-separated fields
#   check Alignment data: no trailing blank lines, no duplicate lines

DTM_slope='data/in/SnowyMountainsSlopeRaster.tif'  #DEM containing slope angle as attribute

In [10]:
# Following alignments approximate vertical shaft by adding a small inclination
# Procedure should be adapted to calculate sloped chainage separately and using this for calculations  #ToDo JK


In [11]:
# Snowy Mountain 2.0 PSP
# study of alternative layouts / alignments

# define alignment

In [12]:
# # for Snowy Mountain 2.0 PSP, data will be defined in Jupyter Notebook, to better document alternatives studied

# # create alignment_df (dataframe) from Alignment csv 
# alignment_df = pd.read_csv(Alignment)

# # delete row if only NA are present in row
# alignment_df = alignment_df.dropna(how = "all")
# # round alignment_df to three decimals
# alignment_df = alignment_df.round(decimals=3)

In [13]:
# # create alignment_df (dataframe) from alignment csv data
# alignment_df = pd.DataFrame.from_records(
# data =[
# ("380", "", 18500.00, 6038594.951, 631021.964, 1078.121),
# ("398", "", 19400.00, 6038611.442, 630122.473, 1076.866),
# ("403", "", 19650.00, 6038458.908, 629930.936, 1076.518),
# ("404", "", 19700.00, 6038422.009, 629897.196, 438.769),
# ("413", "", 20150.00, 6038135.211, 629563.649, 421.364) ], 
# columns=["Point","Type","Station","Northing","Easting","Elevation"] )

# # delete row if only NA are present in row
# alignment_df = alignment_df.dropna(how = "all")
# # round alignment_df to three decimals
# alignment_df = alignment_df.round(decimals=3)

In [14]:
# # JV Ravine Option (U/S PH, vertical shaft)
# # 'Waterway _ Alignment and Invert Profile_Original Design and Alt 1 & 2_Ex....xlsx' 
# #  received 2018.05.02. M. Bieir
# #  Alignment data is from Civil3d and is rigidly output at 50 m station intervlas,
# #  not at alignment tangent points. E.g. vertical shaft is therefore not vertical.
# alignment = {
#     'Station':[17000.00, 17600.00, 17590.00, 17500.00, 18200.00], 
#     'Northing':[6038550.513, 6038110.759, 6038100.759, 6038082.846, 6038217.433],
#     'Easting':[632542.222, 632134.091, 632120.091, 632092.765, 631575.465],
#      #elevations in data are for tunnel invert, elevations adjusted for +4.5m for 9m tunnel diameter 
#     'Elevation':[1106.183, 1105.800, 980.800, 449.500, 446.629]
#     }

In [15]:
# # JV Alt 2 (D/S PH, vertical shaft)
# # 'Waterway _ Alignment and Invert Profile_Original Design and Alt 1 & 2_Ex....xlsx' 
# #  received 2018.05.02. M. Bieir
# #  Alignment data is from Civil3d and is rigidly output at 50 m station intervlas,
# #  not at alignment tangent points. E.g. vertical shaft is therefore not vertical.
# alignment = {
#     'Station':[18500.0, 19400.0, 19650.0, 19700.0, 20+150.0],
#     'Northing':[6038594.951,6038611.442,6038458.908,6038422.009,6038135.211],
#     'Easting':[631021.964,630122.473,629930.936,629897.196,629563.649],
#      #elevations in data are for tunnel invert, elevations adjusted for +4.5m for 9m tunnel diameter 
#     'Elevation':[1078.121,1076.866,1076.518,438.769,421.364]
#     }

In [16]:
# # JV JV1 2018.05.15 (vertical shaft)
# # Snowy_Concept_Check for Confinement_2018 05 15.xlsx received 2018.05.15 from M. Bieri
# alignment = { 
#     'Station':[16956, 19348.7, 19512.6, 19512.6, 19512.6, 19512.6, 19512.6, 19512.6, 19512.6, 19602, 19608],
#     'Northing':[6038616.024, 6038680.380, 6038684.787, 6038684.787, 6038684.787, 6038684.787, 6038684.787, 
#                 6038684.787, 6038684.787, 6038687.191, 6038687.358],
#     'Easting':[632522.964, 630130.630, 629966.831, 629965.831, 629964.831, 629963.831, 
#                629962.831, 629961.831, 629960.831, 629877.463, 629871.245],
#     #elevations in data are for tunnel invert
#     #'Elevation':[1101.00, 1097.51, 1081.12, 1000.0, 900.0, 800.0, 700.0, 600.0, 448.94, 440.00, 432.00]
#     #elevations adjusted for +5.0m for 10m tunnel diameter
#     'Elevation':[1106.00, 1102.51, 1086.12, 1000.0, 900.0, 800.0, 700.0, 600.0, 453.94, 445.00, 437.00]
#     }

In [17]:
# # JV JV2 2018.05.15 (vertical shaft)
# # Snowy_Concept_Check for Confinement_2018 05 15.xlsx received 2018.05.15 from M. Bieri
# # create alignment using dictionary
# alignment = { 
#     'Station':[8606, 16956, 16956, 16956, 16956, 16956, 16956, 16956, 19512.6, 19602, 19608],
#     'Northing':[6038391.483, 6038616.024, 6038616.024, 6038616.024, 6038616.024, 6038616.024, 6038616.024, 
#                 6038616.024, 6038684.787, 6038687.191, 6038687.358],
#     'Easting':[640869.945, 632522.964, 632521.964, 632520.964, 632519.964, 632518.964, 632517.964, 
#                632516.964, 629966.831, 629877.463, 629871.245],
#     #elevations in data are for tunnel invert
#     #'Elevation':[1122.84, 1101.00, 1000.0, 900.0, 800.0, 700.0, 600.0, 448.94, 448.94, 440.00, 432.00]        
#     #elevations adjusted for +5.0m for 10m tunnel diameter    
#     'Elevation':[1127.84, 1106.00, 1000.0, 900.0, 800.0, 700.0, 600.0, 453.94, 453.94, 445.00, 437.00]    
#     }

In [18]:
# JV JV2 2018.05.15 (vertical shaft)
# Snowy_Concept_Check for Confinement_2018 05 15.xlsx received 2018.05.15 from M. Bieri
# create alignment_df (dataframe) from alignment csv data
alignment_df = pd.DataFrame.from_records(
data =[
("", "", 8606, 6038391.483, 640869.945, 1127.84),
("", "", 16956, 6038616.024, 632522.964, 1106.00),
("", "", 16956, 6038616.024, 632521.964, 1000.0),
("", "", 16956, 6038616.024, 632520.964, 900.0),
("", "", 16956, 6038616.024, 632519.964, 800.0),
("", "", 16956, 6038616.024, 632518.964, 700.0),
("", "", 16956, 6038616.024, 632517.964, 600.0),
("", "", 16956, 6038616.024, 632516.964, 453.94),
("", "", 19512.6, 6038684.787, 629966.831, 453.94),
("", "", 19602, 6038687.191, 629877.463, 445.00),
("", "", 19608, 6038687.358, 629871.245, 437.00) ], 
columns=["Point","Type","Station","Northing","Easting","Elevation"] )

# delete row if only NA are present in row
##alignment_df = alignment_df.dropna(how = "all")
# round alignment_df to three decimals
##alignment_df = alignment_df.round(decimals=3)

In [19]:
# #JV JV3 2018.05.15 (inclined shaft)
# # Snowy_Concept_Check for Confinement_2018 05 15.xlsx received 2018.05.15 from M. Bieri
# alignment = { 
#     'Station':[16956, 17005.5, 19262.6, 19512.6, 19602, 19608],
#     'Northing':[6038616.024, 6038616.024, 6038680.380, 6038684.787, 6038687.191, 6038687.358], 
#     'Easting':[632522.964, 632472.964, 630216.831, 629966.831, 629877.463, 629871.245 ],
#     #elevations in data are for tunnel invert
#     #'Elevation':[1101.00, 1097.51, 448.94, 448.94, 440.00, 432.00]
#     #elevations adjusted for +5.0m for 10m tunnel diameter        
#     'Elevation':[1106.00, 1102.51, 453.94, 453.94, 445.00, 437.00]
#     }

In [20]:
# # RTF-1 2018.05.11
# # S2-8200-DRG-XXXXXX Power Waterway Release 1.pdf, 2018.05.11 from F. Takhtemina
# alignment = { 
#     'Station':[15000.0, 16886.428, 17081.8, 17082.8, 17083.8, 17084.8, 17085.8, 18081.8],
#     'Northing':[6038473.48, 6038513.415, 6038547.365, 6038547.365, 6038547.365, 6038547.365, 
#                 6038547.365, 6038721.013],    
#     'Easting':[634520.11, 632634.103, 632441.519, 632440.519, 632439.519, 632438.519, 
#                632437.519, 631456.711], 
#     #elevations in data are for tunnel invert
#     #'Elevation':[1103.9, 1101.1, 1095.0, 1000.0, 800.0, 650.0, 546.2, 448.0]
#     #elevations adjusted for +5.0m for 10m tunnel diameter            
#     'Elevation':[1108.9, 1106.1, 1100.0, 1000.0, 800.0, 650.0, 551.2, 453.0]
# }

In [21]:
# # JV JV1 2018.05.17 (400 m vertical shaft, longer 10% LPT)
# # S2-TD-DRG-RFT_JV1&3 ALT-PP- SHEET 1  received 2018.05.15 from M. Bieri
# alignment = { 
#     'Station':[15000, 17271.925, 17271.925, 19726.777],
#     'Northing':[6038563.42, 6038624.52, 6038624.52, 6038690.53], 
#     'Easting':[634478.26, 632207.15, 632206.15, 629753.18],
#     #elevations in data are for tunnel invert
#     #'Elevation':[1106.11, 1100.17, 685.485, 440.0] 
#     #elevations adjusted for +5.0m for 10m tunnel diameter                
#     'Elevation':[1111.11, 1105.17, 690.485, 445.0] 
#     }

In [22]:
# # use if alignment defined using dictionary

# alignment_df = pd.DataFrame(alignment)
# alignment_df = alignment_df[['Station','Northing','Easting','Elevation']]  #for checking

In [23]:
alignment_df

Point Type  Station     Northing     Easting  Elevation
0               8606.0  6038391.483  640869.945    1127.84
1              16956.0  6038616.024  632522.964    1106.00
2              16956.0  6038616.024  632521.964    1000.00
3              16956.0  6038616.024  632520.964     900.00
4              16956.0  6038616.024  632519.964     800.00
5              16956.0  6038616.024  632518.964     700.00
6              16956.0  6038616.024  632517.964     600.00
7              16956.0  6038616.024  632516.964     453.94
8              19512.6  6038684.787  629966.831     453.94
9              19602.0  6038687.191  629877.463     445.00
10             19608.0  6038687.358  629871.245     437.00

In [24]:
# define required input data

# mapping
crs = {'init': 'epsg:32755'}  #define crs for project Snowy Mountains 2
grass_region = "619000,656000,6029000,6043000"  #map region E1,E2,N1,N2 Snowy Mountains 2

# resolution for analysis
#grass_station_dist = 20  #use for high resolution
grass_station_dist = 50  #use for low resolution
c = 0.5  #ring buffer radius = c*h  (h=overburden)
#res = 3.0  #use for high resolution
res = 25.0  #use for low resolution

# rock properties
density_rock = 27.0  #kN/m3

# hydraulic properties
# upsurge varies along HRT and should be defined as a function                                       #Todo JK
max_static_water_level = 1228.7 + 70  #MASL, include upsurge
print(max_static_water_level)

start_station = alignment_df['Station'][0]  ####
print(start_station)

1298.7
8606.0


In [25]:
# define temporary data
Alignment_shp ='tmp/SnowyMtn2Alignment.shp'  #alignment shp from Alignment
Alignment_grass_csv = 'tmp/SnowyMtn2AlignmentGrass.csv'  #alignment csv fixed for grass
Alignment_line_shp = "tmp/SnowyMtn2AlignmentLine.shp"  #intermediate data
Alignment_stationed_shp = "tmp/SnowyMtn2AlignmentStationed.shp"  #alignment shp containing station points
Alignment_dtm_csv = "tmp/SnowyMtn2AlignmentDTM.csv"  #alignment including terrain elevations at station points
Buffer_shp = "tmp/SnowyMtn2Buffer.shp"  #buffer shp containing ring grid points at a particular station point
Buffer_all_csv = "tmp/SnowyMtn2BufferAll.csv"  # all station point ring buffers written to csv
Buffer_all_shp = "tmp/SnowyMtn2BufferFinal.shp"
Buffer_dtm_csv = "tmp/SnowyMtn2BufferDTM.csv"
Buffer_slope_csv = "tmp/SnowyMtn2BufferSlope.csv"

In [26]:
# define output files


In [27]:
# create stationed alignment as Alignment_stationed_shp                 #ToDo JK: make into stationing function
# from points in alignment_df
#   required grass input data: x, y coordinates at each alignment point
#   grass input for function v.in.line 1) must have x first and y second; 2) no header 
#   grass output: x, y coordinates at each station point along alignment
alignment_df_grass = alignment_df.loc[:,["Easting", "Northing"]]  #x first and y second
# write Alignment_grass_csv
alignment_df_grass.to_csv(Alignment_grass_csv, header=False, index=False)  #no header

# points to line, write output to Alignment_line_shp
processing.runalg("grass7:v.in.lines",Alignment_grass_csv,",",False,
                  grass_region,0,Alignment_line_shp)  #no spaces between commas

# line to station points, ouput segmented polyline to Alignment_stationed_shp
processing.runalg("grass7:v.to.points",Alignment_line_shp,grass_station_dist,1,True,
                  grass_region,-1,0.0001,0,Alignment_stationed_shp)  #no spaces between commas

{'output': 'tmp/SnowyMtn2AlignmentStationed.shp'}

In [28]:
# create alignment_stationed_df from Alignment_stationed_shp            #ToDo JK: make into shp -> df function
#   required output data: x_align, y_align at each station point
alignment_stationed_df = gpd.read_file(Alignment_stationed_shp)

# create columns for x_align, y_align, then delete columns cat_ and geometry
alignment_stationed_df["x_align"] = alignment_stationed_df.geometry.x
alignment_stationed_df["y_align"] = alignment_stationed_df.geometry.y
alignment_stationed_df = alignment_stationed_df.drop(columns =["cat_", "geometry"])

In [29]:
#alignment_stationed_df

In [30]:
# add required fields to alignment_stationed_df

# add "id" 
alignment_stationed_df["id_point"] = alignment_stationed_df.index

# add "distance_stat" referencing length between point n and point n+1
#   is this what is intended??                                                                       ToDo: JK
alignment_stationed_df["distance_stat"] = np.nan
for n in range(0, len(alignment_stationed_df)-1):
    alignment_stationed_df.iloc[n, alignment_stationed_df.columns.get_loc("distance_stat")] = (
        ((alignment_stationed_df.iloc[n +1]["x_align"] - alignment_stationed_df.iloc[n]["x_align"])**2
        +(alignment_stationed_df.iloc[n +1]["y_align"] - alignment_stationed_df.iloc[n]["y_align"])**2 )**(0.5) )

# add "distance_stat_sum"
alignment_stationed_df["distance_stat_sum"] = np.nan
alignment_stationed_df.iloc[0, alignment_stationed_df.columns.get_loc("distance_stat_sum")] = start_station  ####
####for n in range(1, len(alignment_stationed_df) -1):
for n in range(1, len(alignment_stationed_df)):  #refactor !!!
    ####distance = ( alignment_stationed_df.loc[(alignment_stationed_df.id_point.isin(range(0,n +1))), 
    ####                    "distance_stat"] )
    distance = ( alignment_stationed_df.loc[(alignment_stationed_df.id_point.isin(range(0,n))), 
                        "distance_stat"] )
    distances = distance.tolist()
    alignment_stationed_df.iloc[n, alignment_stationed_df.columns.get_loc("distance_stat_sum")] = (
                                                                               sum(distances) +start_station)
    
#alignment_stationed_df.head()
alignment_stationed_df

x_align       y_align  id_point  distance_stat  distance_stat_sum
0    640869.945000  6.038391e+06         0      49.702385        8606.000000
1    640820.260589  6.038393e+06         1      49.702385        8655.702385
2    640770.576179  6.038394e+06         2      49.702385        8705.404769
3    640720.891768  6.038395e+06         3      49.702385        8755.107154
4    640671.207357  6.038397e+06         4      49.702385        8804.809539
5    640621.522946  6.038398e+06         5      49.702385        8854.511923
6    640571.838536  6.038400e+06         6      49.702385        8904.214308
7    640522.154125  6.038401e+06         7      49.702385        8953.916693
8    640472.469714  6.038402e+06         8      49.702385        9003.619077
9    640422.785304  6.038404e+06         9      49.702385        9053.321462
10   640373.100893  6.038405e+06        10      49.702385        9103.023847
11   640323.416482  6.038406e+06        11      49.702385        9152.726232
12   640273.732071  6.038408e+06        12      49.702385        9202.428616
13   640224.047661  6.038409e+06        13      49.702385        9252.131001
14   640174.363250  6.038410e+06        14      49.702385        9301.833386
15   640124.678839  6.038412e+06        15      49.702385        9351.535770
16   640074.994429  6.038413e+06        16      49.702385        9401.238155
17   640025.310018  6.038414e+06        17      49.702385        9450.940540
18   639975.625607  6.038416e+06        18      49.702385        9500.642924
19   639925.941196  6.038417e+06        19      49.702385        9550.345309
20   639876.256786  6.038418e+06        20      49.702385        9600.047694
21   639826.572375  6.038420e+06        21      49.702385        9649.750078
22   639776.887964  6.038421e+06        22      49.702385        9699.452463
23   639727.203554  6.038422e+06        23      49.702385        9749.154848
24   639677.519143  6.038424e+06        24      49.702385        9798.857232
25   639627.834732  6.038425e+06        25      49.702385        9848.559617
26   639578.150321  6.038426e+06        26      49.702385        9898.262002
27   639528.465911  6.038428e+06        27      49.702385        9947.964387
28   639478.781500  6.038429e+06        28      49.702385        9997.666771
29   639429.097089  6.038430e+06        29      49.702385       10047.369156
30   639379.412679  6.038432e+06        30      49.702385       10097.071541
31   639329.728268  6.038433e+06        31      49.702385       10146.773925
32   639280.043857  6.038434e+06        32      49.702385       10196.476310
33   639230.359446  6.038436e+06        33      49.702385       10246.178695
34   639180.675036  6.038437e+06        34      49.702385       10295.881079
35   639130.990625  6.038438e+06        35      49.702385       10345.583464
36   639081.306214  6.038440e+06        36      49.702385       10395.285849
37   639031.621804  6.038441e+06        37      49.702385       10444.988233
38   638981.937393  6.038442e+06        38      49.702385       10494.690618
39   638932.252982  6.038444e+06        39      49.702385       10544.393003
40   638882.568571  6.038445e+06        40      49.702385       10594.095387
41   638832.884161  6.038446e+06        41      49.702385       10643.797772
42   638783.199750  6.038448e+06        42      49.702385       10693.500157
43   638733.515339  6.038449e+06        43      49.702385       10743.202541
44   638683.830929  6.038450e+06        44      49.702385       10792.904926
45   638634.146518  6.038452e+06        45      49.702385       10842.607311
46   638584.462107  6.038453e+06        46      49.702385       10892.309696
47   638534.777696  6.038454e+06        47      49.702385       10942.012080
48   638485.093286  6.038456e+06        48      49.702385       10991.714465
49   638435.408875  6.038457e+06        49      49.702385       11041.416850
50   638385.724464  6.038458e+06        50      49.702385       11091.119234
51   63

In [31]:
# add required field "distance_intermed_align" to alignment_df
alignment_df["distance_intermed_align"] = np.nan

for n in range(0, len(alignment_df) -1):
    alignment_df.iloc[n, alignment_df.columns.get_loc("distance_intermed_align")] = (
        ((alignment_df.iloc[n +1]["Easting"]-alignment_df.iloc[n]["Easting"])**2 
             +(alignment_df.iloc[n +1]["Northing"]-alignment_df.iloc[n]["Northing"])**2 )**(0.5) )
    
#alignment_df.head()
alignment_df

Point Type  Station     Northing     Easting  Elevation  \
0               8606.0  6038391.483  640869.945    1127.84   
1              16956.0  6038616.024  632522.964    1106.00   
2              16956.0  6038616.024  632521.964    1000.00   
3              16956.0  6038616.024  632520.964     900.00   
4              16956.0  6038616.024  632519.964     800.00   
5              16956.0  6038616.024  632518.964     700.00   
6              16956.0  6038616.024  632517.964     600.00   
7              16956.0  6038616.024  632516.964     453.94   
8              19512.6  6038684.787  629966.831     453.94   
9              19602.0  6038687.191  629877.463     445.00   
10             19608.0  6038687.358  629871.245     437.00   

    distance_intermed_align  
0               8350.000627  
1                  1.000000  
2                  1.000000  
3                  1.000000  
4                  1.000000  
5                  1.000000  
6                  1.000000  
7               2551.059911  
8                 89.400328  
9                  6.220242  
10                      NaN

In [32]:
# join alignment_df to alignment_stationed_df
alignment_stationed_df = pd.merge(left= alignment_stationed_df, right = alignment_df, 
                 left_on = ["x_align","y_align"], 
                 right_on = ["Easting","Northing"], how = "left")

# clean up alignment_stationed_df
try:
    alignment_stationed_df = (
        alignment_stationed_df.drop(columns =["Point", "Type", "Northing", "Easting"]) )
except:
    pass

#alignment_stationed_df.head()
alignment_stationed_df

x_align       y_align  id_point  distance_stat  distance_stat_sum  \
0    640869.945000  6.038391e+06         0      49.702385        8606.000000   
1    640820.260589  6.038393e+06         1      49.702385        8655.702385   
2    640770.576179  6.038394e+06         2      49.702385        8705.404769   
3    640720.891768  6.038395e+06         3      49.702385        8755.107154   
4    640671.207357  6.038397e+06         4      49.702385        8804.809539   
5    640621.522946  6.038398e+06         5      49.702385        8854.511923   
6    640571.838536  6.038400e+06         6      49.702385        8904.214308   
7    640522.154125  6.038401e+06         7      49.702385        8953.916693   
8    640472.469714  6.038402e+06         8      49.702385        9003.619077   
9    640422.785304  6.038404e+06         9      49.702385        9053.321462   
10   640373.100893  6.038405e+06        10      49.702385        9103.023847   
11   640323.416482  6.038406e+06        11      49.702385        9152.726232   
12   640273.732071  6.038408e+06        12      49.702385        9202.428616   
13   640224.047661  6.038409e+06        13      49.702385        9252.131001   
14   640174.363250  6.038410e+06        14      49.702385        9301.833386   
15   640124.678839  6.038412e+06        15      49.702385        9351.535770   
16   640074.994429  6.038413e+06        16      49.702385        9401.238155   
17   640025.310018  6.038414e+06        17      49.702385        9450.940540   
18   639975.625607  6.038416e+06        18      49.702385        9500.642924   
19   639925.941196  6.038417e+06        19      49.702385        9550.345309   
20   639876.256786  6.038418e+06        20      49.702385        9600.047694   
21   639826.572375  6.038420e+06        21      49.702385        9649.750078   
22   639776.887964  6.038421e+06        22      49.702385        9699.452463   
23   639727.203554  6.038422e+06        23      49.702385        9749.154848   
24   639677.519143  6.038424e+06        24      49.702385        9798.857232   
25   639627.834732  6.038425e+06        25      49.702385        9848.559617   
26   639578.150321  6.038426e+06        26      49.702385        9898.262002   
27   639528.465911  6.038428e+06        27      49.702385        9947.964387   
28   639478.781500  6.038429e+06        28      49.702385        9997.666771   
29   639429.097089  6.038430e+06        29      49.702385       10047.369156   
30   639379.412679  6.038432e+06        30      49.702385       10097.071541   
31   639329.728268  6.038433e+06        31      49.702385       10146.773925   
32   639280.043857  6.038434e+06        32      49.702385       10196.476310   
33   639230.359446  6.038436e+06        33      49.702385       10246.178695   
34   639180.675036  6.038437e+06        34      49.702385       10295.881079   
35   639130.990625  6.038438e+06        35      49.702385       10345.583464   
36   639081.306214  6.038440e+06        36      49.702385       10395.285849   
37   639031.621804  6.038441e+06        37      49.702385       10444.988233   
38   638981.937393  6.038442e+06        38      49.702385       10494.690618   
39   638932.252982  6.038444e+06        39      49.702385       10544.393003   
40   638882.568571  6.038445e+06        40      49.702385       10594.095387   
41   638832.884161  6.038446e+06        41      49.702385       10643.797772   
42   638783.199750  6.038448e+06        42      49.702385       10693.500157   
43   638733.515339  6.038449e+06        43      49.702385       10743.202541   
44   638683.830929  6.038450e+06        44      49.702385       10792.904926   
45   638634.146518  6.038452e+06        45      49.702385       10842.607311   
46   638584.462107  6.038453e+06        46      49.702385       10892.309696   
47   638534.777696  6.038454e+06        47      49.702385       10942.012080   
48   638485.093286  6.038456e+06        48      49.702385       10991.714465   
49   638435

In [33]:
# get id_points for alignment points in alignment_stationed_df 
#   select points where Elevation of point not NaN
id_points_align =  (
    alignment_stationed_df.loc[(alignment_stationed_df.Elevation.isin(alignment_df["Elevation"])), "id_point"] )
id_points_align= id_points_align.tolist()
id_points_align                                                                         

[0, 168, 169, 170, 171, 172, 173, 174, 226, 228, 229]

In [34]:
len(id_points_align)

11

In [35]:
# prepare intermediated data in alignment_stationed_df required to interpolate alignment elevations

# fill in "Elevation" and "distance_intermed_align" for points in alignment_stationed_df 
#   where points of alignment_points_df != alignment_df

# why is this needed??  (why is Elevation filled in ??)                                                                              ToDo: JK
for n in range(0, len(id_points_align) -1): 
    alignment_stationed_df.loc[(alignment_stationed_df.id_point.isin(range(id_points_align[n] +1, 
                                id_points_align[n +1]))), "Elevation"] = ( 
                                                                    alignment_df["Elevation"][n] )

for n in range(0, len(id_points_align) -1): 
    alignment_stationed_df.loc[(alignment_stationed_df.id_point.isin(range(id_points_align[n] +1, 
                                id_points_align[n +1]))), "distance_intermed_align"] = ( 
                                                        alignment_df["distance_intermed_align"][n] )

# add "distance_intermed_stat" to alignment_stationed_df 
alignment_stationed_df["distance_intermed_stat"] = np.nan

for n in range(0, 1):
    alignment_stationed_df.loc[(alignment_stationed_df.id_point.isin(range(id_points_align[n], 
                                id_points_align[n +1] +1))), "distance_intermed_stat"] =  ( 
                                    alignment_stationed_df["distance_stat_sum"] -start_station )  ####
### for n in range(1, len(id_points_align) -1): 
###     alignment_stationed_df.loc[(alignment_stationed_df.id_point.isin(range(id_points_align[n], 
###                                 id_points_align[n +1]))), "distance_intermed_stat"] = ( 
###                                                     alignment_stationed_df["distance_stat_sum"] - 
###                                                     alignment_df["distance_intermed_align"][n -1] )
for n in range(1, len(id_points_align) -1):
      alignment_stationed_df.loc[(alignment_stationed_df.id_point.isin(range(id_points_align[n] +1, 
                                  id_points_align[n +1] +1))), "distance_intermed_stat"] = ( 
                                             alignment_stationed_df["distance_stat_sum"] - 
                                             alignment_stationed_df["distance_stat_sum"][id_points_align[n]] )
    
#alignment_stationed_df.head()
#alignment_stationed_df

In [36]:
alignment_stationed_df

x_align       y_align  id_point  distance_stat  distance_stat_sum  \
0    640869.945000  6.038391e+06         0      49.702385        8606.000000   
1    640820.260589  6.038393e+06         1      49.702385        8655.702385   
2    640770.576179  6.038394e+06         2      49.702385        8705.404769   
3    640720.891768  6.038395e+06         3      49.702385        8755.107154   
4    640671.207357  6.038397e+06         4      49.702385        8804.809539   
5    640621.522946  6.038398e+06         5      49.702385        8854.511923   
6    640571.838536  6.038400e+06         6      49.702385        8904.214308   
7    640522.154125  6.038401e+06         7      49.702385        8953.916693   
8    640472.469714  6.038402e+06         8      49.702385        9003.619077   
9    640422.785304  6.038404e+06         9      49.702385        9053.321462   
10   640373.100893  6.038405e+06        10      49.702385        9103.023847   
11   640323.416482  6.038406e+06        11      49.702385        9152.726232   
12   640273.732071  6.038408e+06        12      49.702385        9202.428616   
13   640224.047661  6.038409e+06        13      49.702385        9252.131001   
14   640174.363250  6.038410e+06        14      49.702385        9301.833386   
15   640124.678839  6.038412e+06        15      49.702385        9351.535770   
16   640074.994429  6.038413e+06        16      49.702385        9401.238155   
17   640025.310018  6.038414e+06        17      49.702385        9450.940540   
18   639975.625607  6.038416e+06        18      49.702385        9500.642924   
19   639925.941196  6.038417e+06        19      49.702385        9550.345309   
20   639876.256786  6.038418e+06        20      49.702385        9600.047694   
21   639826.572375  6.038420e+06        21      49.702385        9649.750078   
22   639776.887964  6.038421e+06        22      49.702385        9699.452463   
23   639727.203554  6.038422e+06        23      49.702385        9749.154848   
24   639677.519143  6.038424e+06        24      49.702385        9798.857232   
25   639627.834732  6.038425e+06        25      49.702385        9848.559617   
26   639578.150321  6.038426e+06        26      49.702385        9898.262002   
27   639528.465911  6.038428e+06        27      49.702385        9947.964387   
28   639478.781500  6.038429e+06        28      49.702385        9997.666771   
29   639429.097089  6.038430e+06        29      49.702385       10047.369156   
30   639379.412679  6.038432e+06        30      49.702385       10097.071541   
31   639329.728268  6.038433e+06        31      49.702385       10146.773925   
32   639280.043857  6.038434e+06        32      49.702385       10196.476310   
33   639230.359446  6.038436e+06        33      49.702385       10246.178695   
34   639180.675036  6.038437e+06        34      49.702385       10295.881079   
35   639130.990625  6.038438e+06        35      49.702385       10345.583464   
36   639081.306214  6.038440e+06        36      49.702385       10395.285849   
37   639031.621804  6.038441e+06        37      49.702385       10444.988233   
38   638981.937393  6.038442e+06        38      49.702385       10494.690618   
39   638932.252982  6.038444e+06        39      49.702385       10544.393003   
40   638882.568571  6.038445e+06        40      49.702385       10594.095387   
41   638832.884161  6.038446e+06        41      49.702385       10643.797772   
42   638783.199750  6.038448e+06        42      49.702385       10693.500157   
43   638733.515339  6.038449e+06        43      49.702385       10743.202541   
44   638683.830929  6.038450e+06        44      49.702385       10792.904926   
45   638634.146518  6.038452e+06        45      49.702385       10842.607311   
46   638584.462107  6.038453e+06        46      49.702385       10892.309696   
47   638534.777696  6.038454e+06        47      49.702385       10942.012080   
48   638485.093286  6.038456e+06        48      49.702385       10991.714465   
49   638435

In [37]:
# interpolate alignment elevation ("z_align") at all station points and write to alignment_stationed_df

# add variable "z_align" to alignment_stationed_df
alignment_stationed_df["z_align"] = np.nan

for i in range(0, len(alignment_stationed_df)):
    print('i: ',i)
    # alignment points
    if i in id_points_align:
        alignment_stationed_df.iloc[i, alignment_stationed_df.columns.get_loc("z_align")] = ( 
                                                        alignment_stationed_df.iloc[i]["Elevation"] )
    # stationed points
    else:
        id_points_align_plus_point_n = id_points_align
        id_points_align_plus_point_n.append(i)
        id_points_align_plus_point_n.sort()
        m = id_points_align_plus_point_n.index(i) +1  #index of point n +1 (next alignment point)
        n = id_points_align_plus_point_n[m]  #id_point of next alignment point  
        o = id_points_align_plus_point_n.index(i) -1  #index of point n -1 (previous alignment point)
        p = id_points_align_plus_point_n[o]  #id_point of previous alignment point
        print('m,n,o,p: ',m,n,o,p)
        print('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 
                            alignment_stationed_df.iloc[p]["Elevation"],
                            alignment_stationed_df.iloc[n]["Elevation"], 
                            alignment_stationed_df.iloc[i]["distance_intermed_align"],
                            alignment_stationed_df.iloc[i-1]["distance_intermed_stat"])
                                                           
        alignment_stationed_df.iloc[i, alignment_stationed_df.columns.get_loc("z_align")] = ( 
                         alignment_stationed_df.iloc[p]["Elevation"] 
                         +(alignment_stationed_df.iloc[n]["Elevation"] 
                         -alignment_stationed_df.iloc[p]["Elevation"]) 
                             /alignment_stationed_df.iloc[i]["distance_intermed_align"]
                             *alignment_stationed_df.iloc[i]["distance_intermed_stat"] )
                             ####*alignment_stationed_df.iloc[i-1]["distance_intermed_stat"] )
        
        id_points_align_plus_point_n.remove(i)  #needed ??                                           #ToDo JK

alignment_stationed_df = alignment_stationed_df.drop(columns = ["distance_intermed_align"])
alignment_stationed_df = alignment_stationed_df.drop(columns = ["distance_intermed_stat"])
alignment_stationed_df = alignment_stationed_df.drop(columns = ["Elevation"])

#alignment_stationed_df.head()
#alignment_stationed_df

('i: ', 0)
('i: ', 1)
('m,n,o,p: ', 2, 168, 0, 0)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 1127.84, 1106.0, 8350.000627247919, 0.0)
('i: ', 2)
('m,n,o,p: ', 2, 168, 0, 0)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 1127.84, 1106.0, 8350.000627247919, 49.70238468603384)
('i: ', 3)
('m,n,o,p: ', 2, 168, 0, 0)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 1127.84, 1106.0, 8350.000627247919, 99.40476937204403)
('i: ', 4)
('m,n,o,p: ', 2, 168, 0, 0)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 1127.84, 1106.0, 8350.000627247919, 149.10715405796145)
('i: ', 5)
('m,n,o,p: ', 2, 168, 0, 0)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 1127.84, 1106.0, 8350.000627247919, 198.8095387439953)
('i: ', 6)
('m,n,o,p: ', 2, 168, 0, 0)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 1127.84, 1106.0, 8350.000627247919, 248.51192343000548)
('i: ', 7)
('m,n,o,p: ', 2, 168, 0, 0)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 1127.84, 1106.0, 8350.000627247919, 298.2

('i: ', 66)
('m,n,o,p: ', 2, 168, 0, 0)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 1127.84, 1106.0, 8350.000627247919, 3230.655004589935)
('i: ', 67)
('m,n,o,p: ', 2, 168, 0, 0)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 1127.84, 1106.0, 8350.000627247919, 3280.3573892759705)
('i: ', 68)
('m,n,o,p: ', 2, 168, 0, 0)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 1127.84, 1106.0, 8350.000627247919, 3330.059773961979)
('i: ', 69)
('m,n,o,p: ', 2, 168, 0, 0)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 1127.84, 1106.0, 8350.000627247919, 3379.7621586480127)
('i: ', 70)
('m,n,o,p: ', 2, 168, 0, 0)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 1127.84, 1106.0, 8350.000627247919, 3429.464543333932)
('i: ', 71)
('m,n,o,p: ', 2, 168, 0, 0)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 1127.84, 1106.0, 8350.000627247919, 3479.1669280199403)
('i: ', 72)
('m,n,o,p: ', 2, 168, 0, 0)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 1127.84, 1106.0, 8350.00062724

('i: ', 174)
('i: ', 175)
('m,n,o,p: ', 9, 226, 7, 174)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 453.94, 453.94, 2551.0599106759655, 1.0)
('i: ', 176)
('m,n,o,p: ', 9, 226, 7, 174)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 453.94, 453.94, 2551.0599106759655, 49.05884443603645)
('i: ', 177)
('m,n,o,p: ', 9, 226, 7, 174)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 453.94, 453.94, 2551.0599106759655, 98.11768887218932)
('i: ', 178)
('m,n,o,p: ', 9, 226, 7, 174)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 453.94, 453.94, 2551.0599106759655, 147.17653330822577)
('i: ', 179)
('m,n,o,p: ', 9, 226, 7, 174)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 453.94, 453.94, 2551.0599106759655, 196.23537774426222)
('i: ', 180)
('m,n,o,p: ', 9, 226, 7, 174)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 453.94, 453.94, 2551.0599106759655, 245.2942221804151)
('i: ', 181)
('m,n,o,p: ', 9, 226, 7, 174)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 453.94, 453

In [38]:
alignment_stationed_df

x_align       y_align  id_point  distance_stat  distance_stat_sum  \
0    640869.945000  6.038391e+06         0      49.702385        8606.000000   
1    640820.260589  6.038393e+06         1      49.702385        8655.702385   
2    640770.576179  6.038394e+06         2      49.702385        8705.404769   
3    640720.891768  6.038395e+06         3      49.702385        8755.107154   
4    640671.207357  6.038397e+06         4      49.702385        8804.809539   
5    640621.522946  6.038398e+06         5      49.702385        8854.511923   
6    640571.838536  6.038400e+06         6      49.702385        8904.214308   
7    640522.154125  6.038401e+06         7      49.702385        8953.916693   
8    640472.469714  6.038402e+06         8      49.702385        9003.619077   
9    640422.785304  6.038404e+06         9      49.702385        9053.321462   
10   640373.100893  6.038405e+06        10      49.702385        9103.023847   
11   640323.416482  6.038406e+06        11      49.702385        9152.726232   
12   640273.732071  6.038408e+06        12      49.702385        9202.428616   
13   640224.047661  6.038409e+06        13      49.702385        9252.131001   
14   640174.363250  6.038410e+06        14      49.702385        9301.833386   
15   640124.678839  6.038412e+06        15      49.702385        9351.535770   
16   640074.994429  6.038413e+06        16      49.702385        9401.238155   
17   640025.310018  6.038414e+06        17      49.702385        9450.940540   
18   639975.625607  6.038416e+06        18      49.702385        9500.642924   
19   639925.941196  6.038417e+06        19      49.702385        9550.345309   
20   639876.256786  6.038418e+06        20      49.702385        9600.047694   
21   639826.572375  6.038420e+06        21      49.702385        9649.750078   
22   639776.887964  6.038421e+06        22      49.702385        9699.452463   
23   639727.203554  6.038422e+06        23      49.702385        9749.154848   
24   639677.519143  6.038424e+06        24      49.702385        9798.857232   
25   639627.834732  6.038425e+06        25      49.702385        9848.559617   
26   639578.150321  6.038426e+06        26      49.702385        9898.262002   
27   639528.465911  6.038428e+06        27      49.702385        9947.964387   
28   639478.781500  6.038429e+06        28      49.702385        9997.666771   
29   639429.097089  6.038430e+06        29      49.702385       10047.369156   
30   639379.412679  6.038432e+06        30      49.702385       10097.071541   
31   639329.728268  6.038433e+06        31      49.702385       10146.773925   
32   639280.043857  6.038434e+06        32      49.702385       10196.476310   
33   639230.359446  6.038436e+06        33      49.702385       10246.178695   
34   639180.675036  6.038437e+06        34      49.702385       10295.881079   
35   639130.990625  6.038438e+06        35      49.702385       10345.583464   
36   639081.306214  6.038440e+06        36      49.702385       10395.285849   
37   639031.621804  6.038441e+06        37      49.702385       10444.988233   
38   638981.937393  6.038442e+06        38      49.702385       10494.690618   
39   638932.252982  6.038444e+06        39      49.702385       10544.393003   
40   638882.568571  6.038445e+06        40      49.702385       10594.095387   
41   638832.884161  6.038446e+06        41      49.702385       10643.797772   
42   638783.199750  6.038448e+06        42      49.702385       10693.500157   
43   638733.515339  6.038449e+06        43      49.702385       10743.202541   
44   638683.830929  6.038450e+06        44      49.702385       10792.904926   
45   638634.146518  6.038452e+06        45      49.702385       10842.607311   
46   638584.462107  6.038453e+06        46      49.702385       10892.309696   
47   638534.777696  6.038454e+06        47      49.702385       10942.012080   
48   638485.093286  6.038456e+06        48      49.702385       10991.714465   
49   638435

In [39]:
# add required field "z_dtm_align" to alignment_stationed_df 

# list of shapely geometry points                                                #ToDo JK: make df -> shp function           
alignment_stationed_geometry = ( 
    [sp.geometry.Point(row['x_align'], row['y_align']) for key, row in alignment_stationed_df.iterrows()] )
# create alignment_stationed_geometry_df
alignment_stationed_geometry_df = ( 
    gpd.GeoDataFrame(alignment_stationed_df, geometry=alignment_stationed_geometry, crs = crs) )
# write df to Alignment_stationed_shp (overwrite file)
alignment_stationed_geometry_df.to_file(Alignment_stationed_shp, driver='ESRI Shapefile') 

# get DTM values for alignment_points                                     #ToDo JK: make into what.points function
#   write to Alignment_dtm_csv
processing.runalg("grass7:r.what.points",DTM,Alignment_stationed_shp, "NA",",", 500,
                  True,False,False,False,False,grass_region,-1,0.0001,Alignment_dtm_csv)

# create alignment_dtm_df (dataframe) from Alignment_dtm_csv 
alignment_dtm_df = pd.read_csv(Alignment_dtm_csv)

# rename col=tmp... to "z_dtm_align"
alignment_dtm_df_col_tmp = [col for col in alignment_dtm_df.columns if 'tmp' in col]
if len(alignment_dtm_df_col_tmp) != 1:
    print "Extraction of DTM col=tmp did not work properly for alignment. Please check"
    exit()
alignment_dtm_df = alignment_dtm_df.rename(
    columns= {alignment_dtm_df_col_tmp[0]: "z_dtm_align"})

# write alignment_dtm_df["z_dtm_align"] to alignment_stationed_df["z_dtm_align"]
alignment_stationed_df["z_dtm_align"] = alignment_dtm_df["z_dtm_align"]

alignment_stationed_df = alignment_stationed_df.drop(columns = ["geometry"])

#alignment_stationed_df.head()
alignment_stationed_df

x_align       y_align  id_point  distance_stat  distance_stat_sum  \
0    640869.945000  6.038391e+06         0      49.702385        8606.000000   
1    640820.260589  6.038393e+06         1      49.702385        8655.702385   
2    640770.576179  6.038394e+06         2      49.702385        8705.404769   
3    640720.891768  6.038395e+06         3      49.702385        8755.107154   
4    640671.207357  6.038397e+06         4      49.702385        8804.809539   
5    640621.522946  6.038398e+06         5      49.702385        8854.511923   
6    640571.838536  6.038400e+06         6      49.702385        8904.214308   
7    640522.154125  6.038401e+06         7      49.702385        8953.916693   
8    640472.469714  6.038402e+06         8      49.702385        9003.619077   
9    640422.785304  6.038404e+06         9      49.702385        9053.321462   
10   640373.100893  6.038405e+06        10      49.702385        9103.023847   
11   640323.416482  6.038406e+06        11      49.702385        9152.726232   
12   640273.732071  6.038408e+06        12      49.702385        9202.428616   
13   640224.047661  6.038409e+06        13      49.702385        9252.131001   
14   640174.363250  6.038410e+06        14      49.702385        9301.833386   
15   640124.678839  6.038412e+06        15      49.702385        9351.535770   
16   640074.994429  6.038413e+06        16      49.702385        9401.238155   
17   640025.310018  6.038414e+06        17      49.702385        9450.940540   
18   639975.625607  6.038416e+06        18      49.702385        9500.642924   
19   639925.941196  6.038417e+06        19      49.702385        9550.345309   
20   639876.256786  6.038418e+06        20      49.702385        9600.047694   
21   639826.572375  6.038420e+06        21      49.702385        9649.750078   
22   639776.887964  6.038421e+06        22      49.702385        9699.452463   
23   639727.203554  6.038422e+06        23      49.702385        9749.154848   
24   639677.519143  6.038424e+06        24      49.702385        9798.857232   
25   639627.834732  6.038425e+06        25      49.702385        9848.559617   
26   639578.150321  6.038426e+06        26      49.702385        9898.262002   
27   639528.465911  6.038428e+06        27      49.702385        9947.964387   
28   639478.781500  6.038429e+06        28      49.702385        9997.666771   
29   639429.097089  6.038430e+06        29      49.702385       10047.369156   
30   639379.412679  6.038432e+06        30      49.702385       10097.071541   
31   639329.728268  6.038433e+06        31      49.702385       10146.773925   
32   639280.043857  6.038434e+06        32      49.702385       10196.476310   
33   639230.359446  6.038436e+06        33      49.702385       10246.178695   
34   639180.675036  6.038437e+06        34      49.702385       10295.881079   
35   639130.990625  6.038438e+06        35      49.702385       10345.583464   
36   639081.306214  6.038440e+06        36      49.702385       10395.285849   
37   639031.621804  6.038441e+06        37      49.702385       10444.988233   
38   638981.937393  6.038442e+06        38      49.702385       10494.690618   
39   638932.252982  6.038444e+06        39      49.702385       10544.393003   
40   638882.568571  6.038445e+06        40      49.702385       10594.095387   
41   638832.884161  6.038446e+06        41      49.702385       10643.797772   
42   638783.199750  6.038448e+06        42      49.702385       10693.500157   
43   638733.515339  6.038449e+06        43      49.702385       10743.202541   
44   638683.830929  6.038450e+06        44      49.702385       10792.904926   
45   638634.146518  6.038452e+06        45      49.702385       10842.607311   
46   638584.462107  6.038453e+06        46      49.702385       10892.309696   
47   638534.777696  6.038454e+06        47      49.702385       10942.012080   
48   638485.093286  6.038456e+06        48      49.702385       10991.714465   
49   638435

In [40]:
# Add require field "h" to alignment_stationed_df = overburden depth above station point 
alignment_stationed_df["h"] = alignment_stationed_df["z_dtm_align"] - alignment_stationed_df["z_align"] 

#alignment_stationed_df.head()
alignment_stationed_df

x_align       y_align  id_point  distance_stat  distance_stat_sum  \
0    640869.945000  6.038391e+06         0      49.702385        8606.000000   
1    640820.260589  6.038393e+06         1      49.702385        8655.702385   
2    640770.576179  6.038394e+06         2      49.702385        8705.404769   
3    640720.891768  6.038395e+06         3      49.702385        8755.107154   
4    640671.207357  6.038397e+06         4      49.702385        8804.809539   
5    640621.522946  6.038398e+06         5      49.702385        8854.511923   
6    640571.838536  6.038400e+06         6      49.702385        8904.214308   
7    640522.154125  6.038401e+06         7      49.702385        8953.916693   
8    640472.469714  6.038402e+06         8      49.702385        9003.619077   
9    640422.785304  6.038404e+06         9      49.702385        9053.321462   
10   640373.100893  6.038405e+06        10      49.702385        9103.023847   
11   640323.416482  6.038406e+06        11      49.702385        9152.726232   
12   640273.732071  6.038408e+06        12      49.702385        9202.428616   
13   640224.047661  6.038409e+06        13      49.702385        9252.131001   
14   640174.363250  6.038410e+06        14      49.702385        9301.833386   
15   640124.678839  6.038412e+06        15      49.702385        9351.535770   
16   640074.994429  6.038413e+06        16      49.702385        9401.238155   
17   640025.310018  6.038414e+06        17      49.702385        9450.940540   
18   639975.625607  6.038416e+06        18      49.702385        9500.642924   
19   639925.941196  6.038417e+06        19      49.702385        9550.345309   
20   639876.256786  6.038418e+06        20      49.702385        9600.047694   
21   639826.572375  6.038420e+06        21      49.702385        9649.750078   
22   639776.887964  6.038421e+06        22      49.702385        9699.452463   
23   639727.203554  6.038422e+06        23      49.702385        9749.154848   
24   639677.519143  6.038424e+06        24      49.702385        9798.857232   
25   639627.834732  6.038425e+06        25      49.702385        9848.559617   
26   639578.150321  6.038426e+06        26      49.702385        9898.262002   
27   639528.465911  6.038428e+06        27      49.702385        9947.964387   
28   639478.781500  6.038429e+06        28      49.702385        9997.666771   
29   639429.097089  6.038430e+06        29      49.702385       10047.369156   
30   639379.412679  6.038432e+06        30      49.702385       10097.071541   
31   639329.728268  6.038433e+06        31      49.702385       10146.773925   
32   639280.043857  6.038434e+06        32      49.702385       10196.476310   
33   639230.359446  6.038436e+06        33      49.702385       10246.178695   
34   639180.675036  6.038437e+06        34      49.702385       10295.881079   
35   639130.990625  6.038438e+06        35      49.702385       10345.583464   
36   639081.306214  6.038440e+06        36      49.702385       10395.285849   
37   639031.621804  6.038441e+06        37      49.702385       10444.988233   
38   638981.937393  6.038442e+06        38      49.702385       10494.690618   
39   638932.252982  6.038444e+06        39      49.702385       10544.393003   
40   638882.568571  6.038445e+06        40      49.702385       10594.095387   
41   638832.884161  6.038446e+06        41      49.702385       10643.797772   
42   638783.199750  6.038448e+06        42      49.702385       10693.500157   
43   638733.515339  6.038449e+06        43      49.702385       10743.202541   
44   638683.830929  6.038450e+06        44      49.702385       10792.904926   
45   638634.146518  6.038452e+06        45      49.702385       10842.607311   
46   638584.462107  6.038453e+06        46      49.702385       10892.309696   
47   638534.777696  6.038454e+06        47      49.702385       10942.012080   
48   638485.093286  6.038456e+06        48      49.702385       10991.714465   
49   638435

In [41]:
# define make_buffer to get buffer grid points at all station points along alignment
def make_buffer(point, overburden, c, res):
    h = overburden
    if h < 0.0:
        print "Overburden is negative. Please check"
        exit()
    intvls_r = max(int(h*c / res), 1)  #number of intervals along the buffer radius, close enough
    res_r = h*c / intvls_r  #effective resolution along the radius
    buffer = np.array(point)  #initialize buffer, first item is exactly at station point

    # calculate local coordinates for grid along a ring and add to point coor
    for i in range(intvls_r):
        r = c*h - i*res_r
        perim = 2 * r * pi 
        intvls_c = max(int(perim/res), 1)  #number of intervals along a ring, close enough
        item = np.array([0.0, 0.0])  #initialize       
        for j in range(intvls_c):
            item[0] = (sin((2*pi) / intvls_c *(j+1)) *r) + point[0]
            item[1] = (cos((2*pi) / intvls_c *(j+1)) *r) + point[1]
            buffer = np.vstack((buffer, item))  #vstack works with arrays of diff nr of items, append does not        

    return buffer

In [42]:
# create csv file with all buffer points     #ToDo KLK: make check plot of alignment, station points, buffer_all

# point = alignment_stationed_xy
# create alignment_stationed_xy from alignment_stationed_df with x,y of all station points
alignment_stationed_xy = alignment_stationed_df.as_matrix(columns=['x_align','y_align'])
# overburden = alignment_stationed_h
alignment_stationed_h = alignment_stationed_df.as_matrix(columns=['h'])

# initialize buffer_df, buffer_all_df, buffer_all
buffer_all = {}
buffer_df = pd.DataFrame(columns=["id_point", "x_align", "y_align", "z_align", "h" ,"x_buffer", "y_buffer"])
buffer_all_df = pd.DataFrame(columns=["id_point", "x_align", "y_align", "z_align", "h","x_buffer", "y_buffer"])

for n in range(0, len(alignment_stationed_df)):
    ####print('n: ',n)
    buffer_point = make_buffer(point=alignment_stationed_xy[n], overburden=alignment_stationed_h[n], c=c, res=res)
    buffer_all[n] = buffer_df.copy(deep=False)  #copy of initialized buffer_df
    #print("n: ", n)
    #print(buffer_all)
    buffer_all[n]["id_point"] = [n] * len(buffer_point)  #list with len(buffer_point) number of n values) 
    ####buffer_all[n]["stat_sum"] = (  #make stat_sum correct for point n
    ####    [alignment_stationed_df.iloc[n-1, alignment_stationed_df.columns.get_loc("distance_stat_sum")]] * len(buffer_point) ) 
    buffer_all[n]["stat_sum"] = (  #make stat_sum correct for point n
        [alignment_stationed_df.iloc[n, alignment_stationed_df.columns.get_loc("distance_stat_sum")]] * len(buffer_point) ) 
    ####buffer_all[n]["dist_stat"] = (  #make stat_sum correct for point n
    ####    [alignment_stationed_df.iloc[n-1, alignment_stationed_df.columns.get_loc("distance_stat")]] * len(buffer_point) ) 
    buffer_all[n]["dist_stat"] = (  #make stat_sum correct for point n
        [alignment_stationed_df.iloc[n, alignment_stationed_df.columns.get_loc("distance_stat")]] * len(buffer_point) ) 
    buffer_all[n]["x_align"] = ( 
        [alignment_stationed_df.iloc[n, alignment_stationed_df.columns.get_loc("x_align")]] * len(buffer_point) )      
    buffer_all[n]["y_align"] = ( 
        [alignment_stationed_df.iloc[n, alignment_stationed_df.columns.get_loc("y_align")]] * len(buffer_point) )      
    buffer_all[n]["z_align"] = ( 
        [alignment_stationed_df.iloc[n, alignment_stationed_df.columns.get_loc("z_align")]] * len(buffer_point) )           
    buffer_all[n]["h"] = ( 
        [alignment_stationed_df.iloc[n, alignment_stationed_df.columns.get_loc("h")]] * len(buffer_point) )           
    buffer_all[n]["x_buffer"] = buffer_point[0:,0]
    buffer_all[n]["y_buffer"] = buffer_point[0:,1]
    buffer_all_df = pd.concat([buffer_all_df, buffer_all[n]])
    #print(buffer_all_df)

# add variable "id_buffer_point" to buffer_all_df
buffer_all_df = buffer_all_df.reset_index(drop=True)
buffer_all_df["id_buffer_point"] = buffer_all_df.index    

# save buffer_all_df to csv
buffer_all_df.to_csv(Buffer_all_csv, sep=",", na_rep="NaN")

buffer_all_df.head()

dist_stat       h id_point  stat_sum     x_align       x_buffer  \
0  49.702385  232.16        0    8606.0  640869.945  640869.945000   
1  49.702385  232.16        0    8606.0  640869.945  640894.898769   
2  49.702385  232.16        0    8606.0  640869.945  640918.685727   
3  49.702385  232.16        0    8606.0  640869.945  640940.193623   
4  49.702385  232.16        0    8606.0  640869.945  640958.416771   

       y_align      y_buffer  z_align  id_buffer_point  
0  6038391.483  6.038391e+06  1127.84                0  
1  6038391.483  6.038505e+06  1127.84                1  
2  6038391.483  6.038497e+06  1127.84                2  
3  6038391.483  6.038484e+06  1127.84                3  
4  6038391.483  6.038467e+06  1127.84                4

In [43]:
# add required field "z_dtm_buffer" and calcualted "dist" to buffer_all_df 
# add required field "slope" to buffer_all_df 

# buffer_all_df to Buffer_all_shp                                   #ToDo JK: reuse df -> shp function from above
# list of shapely geometry points
buffer_all_geometry = ( 
    [sp.geometry.Point(row['x_buffer'], row['y_buffer']) for key, row in buffer_all_df.iterrows()] )
# create buffer_all_geometry_df
buffer_all_geometry_df = gpd.GeoDataFrame(buffer_all_df, geometry=buffer_all_geometry, crs = crs)
# write df to Buffer_all_shp
buffer_all_geometry_df.to_file(Buffer_all_shp, driver='ESRI Shapefile') 
#print(buffer_all_geometry_df.head())

# get DTM values for Buffer_all_shp                             #ToDo JK: reuse what.points function from above
#   write to Buffer_dtm_csv
processing.runalg("grass7:r.what.points",DTM,Buffer_all_shp, "NA",",", 500,True,False,False,False,False,
                  grass_region,-1,0.0001,Buffer_dtm_csv)

# create buffer_dtm_df (dataframe) from Buffer_dtm_csv
buffer_dtm_df = pd.read_csv(Buffer_dtm_csv)

# rename col=tmp... to "z_dtm_buffer"
buffer_dtm_df_col_tmp = [col for col in buffer_dtm_df.columns if 'tmp' in col]
if len(buffer_dtm_df_col_tmp) != 1:
    print "Extraction of DTM col=tmp did not work properly for buffer. Please check"
    exit()
buffer_dtm_df = buffer_dtm_df.rename(
    columns= {buffer_dtm_df_col_tmp[0]: "z_dtm_buffer"})
#print(buffer_dtm_df.head())

# write buffer_dtm_df["z_dtm"] to buffer_all_df["z_dtm"]
buffer_all_df["z_dtm_buffer"] = buffer_dtm_df["z_dtm_buffer"]
#print(buffer_all_df.head())


# get slope values for Buffer_all_shp
#   write to Buffer_slope_csv
processing.runalg("grass7:r.what.points",DTM_slope,Buffer_all_shp, "NA",",", 500,True,False,False,False,False,
                  grass_region,-1,0.0001,Buffer_slope_csv)

# create buffer_dtm_df (dataframe) from Buffer_dtm_csv
buffer_slope_df = pd.read_csv(Buffer_slope_csv)

# rename col=tmp... to "z_dtm_buffer"
buffer_slope_df_col_tmp = [col for col in buffer_slope_df.columns if 'tmp' in col]
if len(buffer_slope_df_col_tmp) != 1:
    print "Extraction of Slope col=tmp did not work properly for buffer. Please check"
    exit()
buffer_slope_df = buffer_slope_df.rename(
    columns= {buffer_slope_df_col_tmp[0]: "slope"})
#print(buffer_slope_df.head())

# write buffer_dtm_df["z_dtm"] to buffer_all_df["z_dtm"]
buffer_all_df["slope"] = buffer_slope_df["slope"]


# calculate "dist" between each buffer point and associated alignment point 
buffer_all_df["dist"] = (((buffer_all_df["x_align"] - buffer_all_df["x_buffer"])**2 + 
                         (buffer_all_df["y_align"] - buffer_all_df["y_buffer"]) **2) +
                         (buffer_all_df["z_dtm_buffer"] - buffer_all_df["z_align"]) **2) **(0.5)

# clean up
buffer_all_df = buffer_all_df.drop(columns =["geometry"])
buffer_all_df.head()

dist_stat       h id_point  stat_sum     x_align       x_buffer  \
0  49.702385  232.16        0    8606.0  640869.945  640869.945000   
1  49.702385  232.16        0    8606.0  640869.945  640894.898769   
2  49.702385  232.16        0    8606.0  640869.945  640918.685727   
3  49.702385  232.16        0    8606.0  640869.945  640940.193623   
4  49.702385  232.16        0    8606.0  640869.945  640958.416771   

       y_align      y_buffer  z_align  id_buffer_point  z_dtm_buffer  \
0  6038391.483  6.038391e+06  1127.84                0   1360.000000   
1  6038391.483  6.038505e+06  1127.84                1   1373.333333   
2  6038391.483  6.038497e+06  1127.84                2   1373.333333   
3  6038391.483  6.038484e+06  1127.84                3   1373.333333   
4  6038391.483  6.038467e+06  1127.84                4   1374.141769   

       slope        dist  
0  10.045515  232.160000  
1   6.883831  271.553941  
2   6.872921  271.553941  
3   6.872921  271.553941  
4   6.217807  272.285012

In [44]:
#buffer_all_df
buffer_all_df.tail(100)

dist_stat      h id_point      stat_sum     x_align       x_buffer  \
61537        NaN  653.0      229  19608.681108  629871.245  629731.419261   
61538        NaN  653.0      229  19608.681108  629871.245  629742.926109   
61539        NaN  653.0      229  19608.681108  629871.245  629758.124458   
61540        NaN  653.0      229  19608.681108  629871.245  629776.577079   
61541        NaN  653.0      229  19608.681108  629871.245  629797.753123   
61542        NaN  653.0      229  19608.681108  629871.245  629821.043396   
61543        NaN  653.0      229  19608.681108  629871.245  629845.777876   
61544        NaN  653.0      229  19608.681108  629871.245  629871.245000   
61545        NaN  653.0      229  19608.681108  629871.245  629896.523449   
61546        NaN  653.0      229  19608.681108  629871.245  629920.766995   
61547        NaN  653.0      229  19608.681108  629871.245  629942.983105   
61548        NaN  653.0      229  19608.681108  629871.245  629962.262248   
61549        NaN  653.0      229  19608.681108  629871.245  629977.815135   
61550        NaN  653.0      229  19608.681108  629871.245  629989.005027   
61551        NaN  653.0      229  19608.681108  629871.245  629995.373811   
61552        NaN  653.0      229  19608.681108  629871.245  629996.660746   
61553        NaN  653.0      229  19608.681108  629871.245  629992.813146   
61554        NaN  653.0      229  19608.681108  629871.245  629983.988532   
61555        NaN  653.0      229  19608.681108  629871.245  629970.548184   
61556        NaN  653.0      229  19608.681108  629871.245  629953.042352   
61557        NaN  653.0      229  19608.681108  629871.245  629932.187727   
61558        NaN  653.0      229  19608.681108  629871.245  629908.838100   
61559        NaN  653.0      229  19608.681108  629871.245  629883.949407   
61560        NaN  653.0      229  19608.681108  629871.245  629858.540593   
61561        NaN  653.0      229  19608.681108  629871.245  629833.651900   
61562        NaN  653.0      229  19608.681108  629871.245  629810.302273   
61563        NaN  653.0      229  19608.681108  629871.245  629789.447648   
61564        NaN  653.0      229  19608.681108  629871.245  629771.941816   
61565        NaN  653.0      229  19608.681108  629871.245  629758.501468   
61566        NaN  653.0      229  19608.681108  629871.245  629749.676854   
61567        NaN  653.0      229  19608.681108  629871.245  629745.829254   
61568        NaN  653.0      229  19608.681108  629871.245  629747.116189   
61569        NaN  653.0      229  19608.681108  629871.245  629753.484973   
61570        NaN  653.0      229  19608.681108  629871.245  629764.674865   
61571        NaN  653.0      229  19608.681108  629871.245  629780.227752   
61572        NaN  653.0      229  19608.681108  629871.245  629799.506895   
61573        NaN  653.0      229  19608.681108  629871.245  629821.723005   
61574        NaN  653.0      229  19608.681108  629871.245  629845.966551   
61575        NaN  653.0      229  19608.681108  629871.245  629871.245000   
61576        NaN  653.0      229  19608.681108  629871.245  629896.228769   
61577        NaN  653.0      229  19608.681108  629871.245  629919.642715   
61578        NaN  653.0      229  19608.681108  629871.245  629940.015655   
61579        NaN  653.0      229  19608.681108  629871.245  629956.067482   
61580        NaN  653.0      229  19608.681108  629871.245  629966.789601   
61581        NaN  653.0      229  19608.681108  629871.245  629971.508301   
61582        NaN  653.0      229  19608.681108  629871.245  629969.927088   
61583        NaN  653.0      229  19608.681108  629871.245  629962.145318   
61584        NaN  653.0      229  19608.681108  629871.245  629948.651946   
61585        NaN  653.0      229  19608.681108  629871.245  629930.294811   
61586        NaN  653.0      229  19608.681108  629871.245  629908.227359   
61587        NaN  653.0      229  19608.681108  629871.245  629883.836169   
615

In [45]:
# calculate minimum distance to terrain in each buffer ring
                                                #ToDo KLK: make check plot of id_buffer_points with "min_dist"
                                                #ToDo JK: add station field
buffer_all_df["min_dist"] = np.nan

for n in range(0, len(alignment_stationed_df)):
    buffer_all_df_sel = buffer_all_df.loc[(buffer_all_df["id_point"] == n),]
    dist_idxmin=buffer_all_df_sel['dist'].idxmin()
    buffer_all_df.loc[(buffer_all_df["id_buffer_point"] == dist_idxmin), "min_dist"] = "MIN"

buffer_all_df.to_csv(Buffer_all_csv, header=True, index=False)  #no header
#buffer_all_df
buffer_all_df.tail(100)

#buffer_all_df.loc[(buffer_all_df["min_dist"] == "MIN"),]

dist_stat      h id_point      stat_sum     x_align       x_buffer  \
61537        NaN  653.0      229  19608.681108  629871.245  629731.419261   
61538        NaN  653.0      229  19608.681108  629871.245  629742.926109   
61539        NaN  653.0      229  19608.681108  629871.245  629758.124458   
61540        NaN  653.0      229  19608.681108  629871.245  629776.577079   
61541        NaN  653.0      229  19608.681108  629871.245  629797.753123   
61542        NaN  653.0      229  19608.681108  629871.245  629821.043396   
61543        NaN  653.0      229  19608.681108  629871.245  629845.777876   
61544        NaN  653.0      229  19608.681108  629871.245  629871.245000   
61545        NaN  653.0      229  19608.681108  629871.245  629896.523449   
61546        NaN  653.0      229  19608.681108  629871.245  629920.766995   
61547        NaN  653.0      229  19608.681108  629871.245  629942.983105   
61548        NaN  653.0      229  19608.681108  629871.245  629962.262248   
61549        NaN  653.0      229  19608.681108  629871.245  629977.815135   
61550        NaN  653.0      229  19608.681108  629871.245  629989.005027   
61551        NaN  653.0      229  19608.681108  629871.245  629995.373811   
61552        NaN  653.0      229  19608.681108  629871.245  629996.660746   
61553        NaN  653.0      229  19608.681108  629871.245  629992.813146   
61554        NaN  653.0      229  19608.681108  629871.245  629983.988532   
61555        NaN  653.0      229  19608.681108  629871.245  629970.548184   
61556        NaN  653.0      229  19608.681108  629871.245  629953.042352   
61557        NaN  653.0      229  19608.681108  629871.245  629932.187727   
61558        NaN  653.0      229  19608.681108  629871.245  629908.838100   
61559        NaN  653.0      229  19608.681108  629871.245  629883.949407   
61560        NaN  653.0      229  19608.681108  629871.245  629858.540593   
61561        NaN  653.0      229  19608.681108  629871.245  629833.651900   
61562        NaN  653.0      229  19608.681108  629871.245  629810.302273   
61563        NaN  653.0      229  19608.681108  629871.245  629789.447648   
61564        NaN  653.0      229  19608.681108  629871.245  629771.941816   
61565        NaN  653.0      229  19608.681108  629871.245  629758.501468   
61566        NaN  653.0      229  19608.681108  629871.245  629749.676854   
61567        NaN  653.0      229  19608.681108  629871.245  629745.829254   
61568        NaN  653.0      229  19608.681108  629871.245  629747.116189   
61569        NaN  653.0      229  19608.681108  629871.245  629753.484973   
61570        NaN  653.0      229  19608.681108  629871.245  629764.674865   
61571        NaN  653.0      229  19608.681108  629871.245  629780.227752   
61572        NaN  653.0      229  19608.681108  629871.245  629799.506895   
61573        NaN  653.0      229  19608.681108  629871.245  629821.723005   
61574        NaN  653.0      229  19608.681108  629871.245  629845.966551   
61575        NaN  653.0      229  19608.681108  629871.245  629871.245000   
61576        NaN  653.0      229  19608.681108  629871.245  629896.228769   
61577        NaN  653.0      229  19608.681108  629871.245  629919.642715   
61578        NaN  653.0      229  19608.681108  629871.245  629940.015655   
61579        NaN  653.0      229  19608.681108  629871.245  629956.067482   
61580        NaN  653.0      229  19608.681108  629871.245  629966.789601   
61581        NaN  653.0      229  19608.681108  629871.245  629971.508301   
61582        NaN  653.0      229  19608.681108  629871.245  629969.927088   
61583        NaN  653.0      229  19608.681108  629871.245  629962.145318   
61584        NaN  653.0      229  19608.681108  629871.245  629948.651946   
61585        NaN  653.0      229  19608.681108  629871.245  629930.294811   
61586        NaN  653.0      229  19608.681108  629871.245  629908.227359   
61587        NaN  653.0      229  19608.681108  629871.245  629883.836169   
615

In [46]:
# calculate hydraulic confinement safety factor at each station point
#   required input data: reference maximum water pressure elevation (static or dynamic ??) 


buffer_all_df_sel = buffer_all_df.loc[(buffer_all_df["min_dist"] == "MIN"),]


dist = array(buffer_all_df_sel['dist'])
slope = array(buffer_all_df_sel['slope'])
z_align = array(buffer_all_df_sel['z_align'])
stat_sum = array(buffer_all_df_sel['stat_sum'])
stat_sum[0] = 0  #correction for station_stat_sum being for n-1 above (to be fixed above)

FS = (dist * density_rock * cos(slope*pi/180.)) / ((max_static_water_level - z_align) * 9.805)
print(FS)
print(stat_sum)

buffer_all_df_sel["FS"] = np.nan
for n in range(0, len(buffer_all_df_sel)):
    buffer_all_df_sel.iloc[n, buffer_all_df_sel.columns.get_loc("FS")] = FS[n]

buffer_all_df_sel = buffer_all_df_sel.drop(columns =["x_align", "y_align", "min_dist", "id_buffer_point"])
    

[3.54114668 3.49314414 3.47240143 3.43574457 3.37744425 3.3674053
 3.30225506 3.27535583 3.28954659 3.21668682 3.07169953 3.02803203
 2.96017898 2.96642158 2.90129573 2.9409886  2.92344206 2.94021181
 2.89975378 2.99931201 3.05730237 3.06715167 3.05590371 3.08543643
 3.13132217 3.18462606 3.22886557 3.29596181 3.29718267 3.29663217
 3.31342088 3.33590497 3.34306429 3.34334018 3.35535056 3.39175482
 3.43042241 3.44267847 3.44675906 3.42966802 3.30739257 3.1773759
 3.21313791 3.20117465 3.22279101 3.22879867 3.28332455 3.35517202
 3.45953728 3.50125155 3.60608165 3.70464358 3.70415589 3.79374198
 3.85746707 3.80685431 3.7576265  3.76326334 3.75579477 3.75505314
 3.79862048 3.82891424 3.81433002 3.81328324 3.82779859 3.83542155
 3.89944863 3.85986331 3.97585704 4.10636202 4.35357789 4.59843709
 4.77007473 4.78544636 4.83639215 4.77383148 4.72014209 4.73898151
 4.76740813 4.8781507  4.90601478 4.97051168 5.01128395 5.06799087
 5.16061522 5.23283329 5.18104442 5.16897389 5.155319   5.178208

In [47]:
dist = 103.2
z_align = 1099.3
slope = 0
FS = (dist * density_rock * cos(slope*pi/180.)) / ((max_static_water_level - z_align) * 9.805)
print(FS)
print(max_static_water_level)

1.4251832499026906
1298.7


In [48]:
#buffer_all_df_sel["stat_sum"]
#buffer_all_df_sel.iloc[1, buffer_all_df_sel.columns.get_loc("stat_sum")]
buffer_all_df_sel.iloc[1, buffer_all_df_sel.columns.get_loc("FS")]


3.4931441390526428

In [49]:
buffer_all_df_sel
#buffer_all_df_sel.tail(9)

dist_stat           h id_point      stat_sum       x_buffer  \
68     49.702385  232.160000        0   8606.000000  640857.353694   
136    49.702385  222.290000        1   8655.702385  640796.196991   
203    49.702385  219.490885        2   8705.404769  640746.815593   
269    49.702385  215.883333        3   8755.107154  640720.891768   
273    49.702385  210.832937        4   8804.809539  640671.207357   
338    49.702385  210.198253        5   8854.511923  640621.522946   
462    49.702385  206.633835        6   8904.214308  640571.838536   
525    49.702385  205.070000        7   8953.916693  640522.154125   
529    49.702385  205.811747        8   9003.619077  640472.469714   
644    49.702385  206.663333        9   9053.321462  640378.041379   
690    49.702385  198.460000       10   9103.023847  640311.983182   
704    49.702385  193.590000       11   9152.726232  640323.416482   
794    49.702385  188.720000       12   9202.428616  640287.379161   
840    49.702385  188.850000       13   9252.131001  640237.704151   
845    49.702385  183.980000       14   9301.833386  640174.363250   
891    49.702385  184.571766       15   9351.535770  640124.678839   
937    49.702385  184.240000       16   9401.238155  640074.994429   
983    49.702385  184.826663       17   9450.940540  640025.310018   
1029   49.702385  184.500000       18   9500.642924  639975.625607   
1116   49.702385  194.630000       19   9550.345309  639948.878562   
1172   49.702385  194.760000       20   9600.047694  639876.256786   
1221   49.702385  194.890000       21   9649.750078  639826.572375   
1222   49.702385  192.948749       22   9699.452463  639776.887964   
1271   49.702385  195.150000       23   9749.154848  639727.203554   
1363   49.702385  198.483444       24   9798.857232  639700.910641   
1427   49.702385  203.144481       25   9848.559617  639649.825767   
1489   49.702385  205.540000       26   9898.262002  639600.400679   
1495   49.702385  208.874101       27   9947.964387  639528.465911   
1621   49.702385  209.494126       28   9997.666771  639478.781500   
1686   49.702385  209.930000       29  10047.369156  639429.097089   
1751   49.702385  212.060000       30  10097.071541  639379.412679   
1817   49.702385  212.856667       31  10146.773925  639329.728268   
1821   49.702385  212.626165       32  10196.476310  639280.043857   
1887   49.702385  212.700000       33  10246.178695  639230.359446   
1953   49.702385  213.722857       34  10295.881079  639180.675036   
2080   49.702385  216.710000       35  10345.583464  639154.450171   
2086   49.702385  218.760492       36  10395.285849  639081.306214   
2153   49.702385  219.697273       37  10444.988233  639031.621804   
2220   49.702385  220.100000       38  10494.690618  638981.937393   
2287   49.702385  219.150492       39  10544.393003  638932.252982   
2410   49.702385  218.377501       40  10594.095387  638831.521944   
2421   49.702385  207.490000       41  10643.797772  638832.884161   
2486   49.702385  205.813664       42  10693.500157  638783.199750   
2549   49.702385  205.138011       43  10743.202541  638733.515339   
2612   49.702385  206.724732       44  10792.904926  638683.830929   
2675   49.702385  208.010000       45  10842.607311  638634.146518   
2740   49.702385  212.282502       46  10892.309696  638584.462107   
2867   49.702385  218.270000       47  10942.012080  638558.406117   
2938   49.702385  225.066667       48  10991.714465  638512.521258   
3009   49.702385  228.530000       49  11041.416850  638463.258909   
3081   49.702385  238.660000       50  11091.119234  638409.048452   
3162   49.702385  243.790000       51  11140.821619  638336.040054   
3232   49.702385  244.777498       52  11190.524004  638310.277487   
3295   49.702385  249.050000       53  11240.226388  638282.941287   
3316   49.702385  249.180000       54  11289.928773  638186.986821   
3466   49.702385  249.310000       55  11339.631158  638123.780966   
3542   49.702385 

In [50]:
z_dtm_align = go.Scatter(
    x=alignment_stationed_df['distance_stat_sum'].tolist(),
    y=alignment_stationed_df['z_dtm_align'].tolist(),
    name = "Terrain",
    mode='lines',
    line=dict(width=0.5,
              color='rgb(196, 97, 26)'),
    fill='tonexty'
)
####print('z_dtm_align',z_dtm_align)

z_align_line = go.Scatter(
    x=alignment_stationed_df['distance_stat_sum'].tolist(),
    y=alignment_stationed_df['z_align'].tolist(),
    line=dict(width=3,
              color='rgb(0, 0, 0)'),
    name ="Tunnel"
)

data = [z_dtm_align, z_align_line]

layout = go.Layout(
    title='Longitudinal Section',
    showlegend=False,
    xaxis=dict(
        title= "Stationing",
    ),
    yaxis=dict(
        title = "m a.s.l.",
        #range = [300,800]  #need a procedure to automate this
    ),
    margin=dict(
        #l=50,
        b=40
    ),
    height=400,
)

fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig, show_link=False, filename='stacked-area-plot')



# initialize variables 
x_data = []
y_data = []
traces = []
annotations = []

fs = buffer_all_df_sel['FS'].tolist(),
c_fs = []
for i in range(len(buffer_all_df_sel.index)):
    if fs[0][i] <= 1.3:
        c_fs.append('red')
    elif 1.3 < fs[0][i] < 1.5:
        c_fs.append('yellow')
    else:
        c_fs.append('green')
slope = buffer_all_df_sel['slope'].tolist(),
c_slope = []
for i in range(len(buffer_all_df_sel.index)):
    if slope[0][i] > 30:
        c_slope.append('red')
    else:
        c_slope.append('green')        

x_data = [buffer_all_df_sel['dist_stat'].tolist()]
# x_data = [buffer_all_df_sel['dist_stat'].tolist(),
#           buffer_all_df_sel['dist_stat'].tolist()]

y_data = ['hydraulic confinement']
# y_data = ['slope',
#           'hydraulic confinement']

for i in range(0, len(x_data[0])):
    for xd, yd in zip(x_data, y_data):
        traces.append(go.Bar(
            x=[xd[i]],
            y=[yd],
            width = 0.3,
            orientation='h',
            marker=dict(
                color = c_fs[i],
            ),
            hoverinfo = 'none',
        ))
        
layout = go.Layout(
    xaxis=dict(
        showgrid=False,
        showline=False,
        showticklabels=False,
        zeroline=False,
        domain=[0.08, 1]  #horizontal extent of bar
    ),
    yaxis=dict(
        showgrid=False,
        showline=False,
        showticklabels=False,
        zeroline=False,
    ),
    barmode='stack',
    #paper_bgcolor='rgb(248, 248, 255)',
    #plot_bgcolor='rgb(248, 248, 255)',
    margin=dict(
        l=0,
        r=0,
        t=0,
        b=0
    ),
    showlegend=False,
    width=945,
    height=70,
)

for yd, xd in zip(y_data, x_data):
    # labeling the y-axis
    annotations.append(dict(xref='paper', yref='y',
                            x=0.09, y=yd, #x is position of text
                            xanchor='left',
                            text=str(yd),
                            font=dict(family='Arial', size=14,
                                      #color='rgb(67, 67, 67)'),
                                      color='white'),
                            showarrow=False, align='left'))
layout['annotations'] = annotations

fig = go.Figure(data=traces, layout=layout)
plotly.offline.iplot(fig, show_link=False, config=dict(displayModeBar=False), filename='bar-colorscale')

In [51]:
buffer_all_df_sel.loc[:, ['stat_sum', 'z_align', 'h', 'z_dtm_buffer', 'dist', 'slope', 'FS']].round(2).tail(200)

stat_sum  z_align       h  z_dtm_buffer    dist  slope    FS
1751   10097.07  1123.94  212.06       1333.20  210.94   4.51  3.31
1817   10146.77  1123.81  212.86       1334.46  212.32   3.76  3.34
1821   10196.48  1123.68  212.63       1336.31  212.63   2.13  3.34
1887   10246.18  1123.55  212.70       1336.25  212.70   1.19  3.34
1953   10295.88  1123.42  213.72       1337.14  213.72   2.12  3.36
2080   10345.58  1123.29  216.71       1338.00  216.41   3.30  3.39
2086   10395.29  1123.16  218.76       1341.92  218.76   1.56  3.43
2153   10444.99  1123.03  219.70       1342.73  219.70   1.49  3.44
2220   10494.69  1122.90  220.10       1343.00  220.10   1.27  3.45
2287   10544.39  1122.77  219.15       1341.92  219.15   1.00  3.43
2410   10594.10  1122.64  218.38       1330.00  214.43   9.54  3.31
2421   10643.80  1122.51  207.49       1330.00  207.49  11.54  3.18
2486   10693.50  1122.38  205.81       1328.19  205.81   1.55  3.21
2549   10743.20  1122.25  205.14       1327.39  205.14   0.69  3.20
2612   10792.90  1122.12  206.72       1328.84  206.72   1.43  3.22
2675   10842.61  1121.99  208.01       1330.00  208.01   5.06  3.23
2740   10892.31  1121.86  212.28       1334.14  212.28   6.65  3.28
2867   10942.01  1121.73  218.27       1336.67  216.66   5.61  3.36
2938   10991.71  1121.60  225.07       1344.14  224.31   7.30  3.46
3009   11041.42  1121.47  228.53       1346.67  227.00   6.93  3.50
3081   11091.12  1121.34  238.66       1354.14  234.71   8.28  3.61
3162   11140.82  1121.21  243.79       1360.00  240.73   7.29  3.70
3232   11190.52  1121.08  244.78       1360.00  240.87   7.29  3.70
3295   11240.23  1120.95  249.05       1360.00  247.03   7.55  3.79
3316   11289.93  1120.82  249.18       1370.00  249.18   0.00  3.86
3466   11339.63  1120.69  249.31       1366.67  247.94   7.01  3.81
3542   11389.33  1120.56  246.11       1363.33  244.71   6.62  3.76
3618   11439.04  1120.43  249.57       1365.00  246.55   8.83  3.76
3695   11488.74  1120.30  249.70       1365.00  246.68   9.47  3.76
3772   11538.44  1120.17  249.83       1365.00  246.81   9.47  3.76
3838   11588.14  1120.04  249.96       1360.00  247.96   6.32  3.80
3943   11637.85  1119.91  253.42       1370.00  251.37   8.51  3.83
4040   11687.55  1119.78  256.89       1370.00  251.54   9.84  3.81
4133   11737.25  1119.65  255.35       1370.00  251.65   9.84  3.81
4228   11786.95  1119.52  255.48       1370.00  251.78   8.41  3.83
4325   11836.66  1119.39  260.61       1370.00  251.96   7.60  3.84
4416   11886.36  1119.26  270.74       1370.00  256.52   7.87  3.90
4521   11936.06  1119.13  284.20       1380.00  266.99  19.48  3.86
4609   11985.76  1119.00  291.00       1380.00  275.21  19.48  3.98
4721   12035.46  1118.87  301.13       1390.00  289.11  21.95  4.11
4895   12085.17  1118.74  311.26       1410.00  295.84  15.91  4.35
4993   12134.87  1118.61  316.39       1410.00  309.89  13.96  4.60
5173   12184.57  1118.48  321.52       1430.00  316.10   9.02  4.77
5312   12234.27  1118.35  321.65       1430.00  316.23   7.64  4.79
5461   12283.98  1118.22  321.78       1436.67  319.57   7.30  4.84
5593   12333.68  1118.09  321.91       1430.00  316.49   8.39  4.77
5737   12383.38  1117.96  317.04       1430.00  313.16   8.39  4.72
5874   12433.08  1117.83  316.31       1430.00  313.28   6.50  4.74
6013   12482.79  1117.70  318.97       1433.33  316.75   8.39  4.77
6127   12532.49  1117.57  327.43       1430.00  322.98   6.55  4.88
6287   12582.19  1117.44  332.56       1440.00  327.29   9.35  4.91
6414   12631.89  1117.31  337.69       1436.67  330.33   7.61  4.97
6581   12681.60  1117.18  342.82       1450.00  337.69  11.98  5.01
6732   12731.30  1117.05  347.95       1455.00  342.89  12.84  5.07
6895   12781.00  1116.92  355.15       1455.00  346.54  10.56  5.16
7073   12830.70  1116.79  349.88       1462.50  346.94   4.87  5.23
7222   12880.41  1116.66  343.34       1458.33  342.87   2.64  5.18
7370   12930.11  1116.53  342.04       1457.30  341.96   0.45  

In [52]:
alignment_stationed_line_plot = go.Scatter(
    x=alignment_stationed_df['x_align'].tolist(),
    y=alignment_stationed_df['y_align'].tolist(),
    line=dict(width=3,
              color='rgb(0, 0, 0)'),
    name ="alignment_stationed_line"
)

alignment_point_plot = go.Scatter(
    x=alignment_df['Easting'].tolist(),
    y=alignment_df['Northing'].tolist(),
    name ="alignment_point",
    mode = "markers",
    marker = dict(
        size = 20,
        color = 'rgb(255, 153, 153)'
    )
)

alignment_stationed_point_plot = go.Scatter(
    x=alignment_stationed_df['x_align'].tolist(),
    y=alignment_stationed_df['y_align'].tolist(),
    mode = "markers",
    name ="alignment_stationed_point",
    marker = dict(
        size = 6,
        color = 'rgb(255, 0, 0)'
    )
)

buffer_all_df_point_plot = go.Scatter(
    x=buffer_all_df['x_buffer'].tolist(),
    y=buffer_all_df['y_buffer'].tolist(),
    mode = "markers",
    name ="buffer_all_point",
     marker = dict(
        size = 6,
        color = 'rgba(0, 0, 153, 0.005)'  #use for high resolution
        #color = 'rgba(0, 0, 153, 0.4)'  #use for low resolution
    )
)
buffer_min_df_point_plot = go.Scatter(
    x=buffer_all_df_sel['x_buffer'].tolist(),
    y=buffer_all_df_sel['y_buffer'].tolist(),
    mode = "markers",
    name ="buffer_min",
     marker = dict(
        size = 8,
        color = 'rgb(0, 0, 153)'
    )
)

data = [alignment_stationed_line_plot, alignment_point_plot, alignment_stationed_point_plot, 
        buffer_all_df_point_plot, buffer_min_df_point_plot]


fig = go.Figure(data=data)
plotly.offline.iplot(fig, show_link=False, filename='stacked-area-plot')

ToDo: check that grid width is adequate (display grid points on graphic very light)
ToDo: overlay project layout as basemap (opague)

In [53]:
alignment_df.head(20)

Point Type  Station     Northing     Easting  Elevation  \
0               8606.0  6038391.483  640869.945    1127.84   
1              16956.0  6038616.024  632522.964    1106.00   
2              16956.0  6038616.024  632521.964    1000.00   
3              16956.0  6038616.024  632520.964     900.00   
4              16956.0  6038616.024  632519.964     800.00   
5              16956.0  6038616.024  632518.964     700.00   
6              16956.0  6038616.024  632517.964     600.00   
7              16956.0  6038616.024  632516.964     453.94   
8              19512.6  6038684.787  629966.831     453.94   
9              19602.0  6038687.191  629877.463     445.00   
10             19608.0  6038687.358  629871.245     437.00   

    distance_intermed_align  
0               8350.000627  
1                  1.000000  
2                  1.000000  
3                  1.000000  
4                  1.000000  
5                  1.000000  
6                  1.000000  
7               2551.059911  
8                 89.400328  
9                  6.220242  
10                      NaN